In [2]:
import sqlite3
import pandas as pd

In [3]:
import re

In [4]:
pd.set_option("display.max_colwidth",500)
pd.set_option("display.max_rows",500)
features_to_show = ["crawl_id", "func_name", "top_level_url", "symbol", "operation", "value", "arguments"]

In [5]:
DB = 'sample_2018-06_1m_stateless_census_crawl.sqlite'

In [6]:
con = sqlite3.connect(DB)

In [7]:
con.row_factory = sqlite3.Row
cur = con.cursor()
js = pd.read_sql_query("SELECT * FROM javascript", con)

In [34]:
# js

In [8]:
js[js.operation == "call"].symbol.value_counts().head(15)

window.Storage.getItem                  46851
window.Storage.setItem                  18104
window.Storage.removeItem               13812
CanvasRenderingContext2D.fill            7258
CanvasRenderingContext2D.save            7074
CanvasRenderingContext2D.restore         7070
HTMLCanvasElement.getContext             4208
window.Storage.key                       3689
CanvasRenderingContext2D.measureText     3103
CanvasRenderingContext2D.stroke          2393
CanvasRenderingContext2D.arc             1558
CanvasRenderingContext2D.fillRect        1371
CanvasRenderingContext2D.clip            1327
CanvasRenderingContext2D.fillText         858
CanvasRenderingContext2D.rotate           537
Name: symbol, dtype: int64

In [9]:
js[(js.operation == "call") &
   (js.symbol == "CanvasRenderingContext2D.fillText")
  ].arguments.value_counts().head(10)

{"0":"Cwm fjordbank glyphs vext quiz, 😃","1":2,"2":15}    74
{"0":"Cwm fjordbank glyphs vext quiz, 😃","1":4,"2":45}    74
{"0":"!image!","1":4,"2":17}                              39
{"0":"!image!","1":2,"2":15}                              39
{"0":"!H71JCaj)]# 1@#","1":4,"2":8}                       19
{"0":"Soft Ruddy Foothold 2","1":2,"2":2}                 19
{"0":"🇺​🇳","1":0,"2":0}                                   18
{"0":"🇺🇳","1":0,"2":0}                                    18
{"0":"🕴​♀️","1":0,"2":0}                                  14
{"0":"09:30","1":5,"2":130}                               14
Name: arguments, dtype: int64

<b> Criteria 1 from Englehardt & Narayanan, 2016: </b>

To be a fingerprinting candidate: "1.The canvas element’s height and width properties must
not be set below 16 px."

In [10]:
def width_height_finder(data):
    w = re.compile('[^(line)]width', re.IGNORECASE)
    h = re.compile('[^(line)]height', re.IGNORECASE)
    ww = w.search(data)
    hh = h.search(data)
    if ww!= None:
        return data
    elif hh!=None:
        return data

In [11]:
l = list(map(width_height_finder, list(js[js.operation == "set"].symbol)))
l = [x for x in l if x is not None]

In [12]:
set(l)

{'HTMLCanvasElement.height', 'HTMLCanvasElement.width'}

In [13]:
MIN_CANVAS_IMAGE_WIDTH = 16
MIN_CANVAS_IMAGE_HEIGHT = 16


canvas_size = js[js.symbol.isin(["HTMLCanvasElement.width", "HTMLCanvasElement.height"])].value.astype(float)
index_size_filter = canvas_size.where(canvas_size > MIN_CANVAS_IMAGE_HEIGHT).dropna().index

In [14]:
index_size_filter

Int64Index([   638,    639,   1138,   1139,   1142,   1143,   1192,   1193,
              1241,   1242,
            ...
            501091, 501092, 501186, 501187, 501190, 501191, 501196, 501197,
            501200, 501201],
           dtype='int64', length=7559)

In [15]:
# js.iloc[index_size_filter][features_to_show]

crawl_id                            func_name  \
638           14      [87]/i</e.prototype.getCanvasFp   
639           14      [87]/i</e.prototype.getCanvasFp   
1138           3               h.createCanvasAndSolve   
1139           3               h.createCanvasAndSolve   
1142           3                                    g   
1143           3                                    g   
1192           3                                    g   
1193           3                                    g   
1241           3               h.createCanvasAndSolve   
1242           3               h.createCanvasAndSolve   
1245           3                                    g   
1246           3                                    g   
1300           3                                    g   
1301           3                                    g   
2083          12                                y.ecn   
2084          12                                y.ecn   
2230           4                  r.canvasFingerprint   
2231           4                  r.canvasFingerprint   
2706           6              e.prototype.getCanvasFp   
2707           6              e.prototype.getCanvasFp   
4450          13                                y.ecn   
4451          13                                y.ecn   
5042          11                                    v   
5044          11                                    v   
5085          11                                    v   
5086          11                                    v   
5142          11                                    v   
5143          11                                    v   
5169          11                                    v   
5170          11                                    v   
5392          13                                    v   
5393          13                                    v   
5635           5                                    v   
5636           5                                    v   
5721           5                                    v   
5722           5                                    v   
5751           5                                    v   
5752           5                                    v   
8748           4                                y.ecn   
8749           4                                y.ecn   
15272         14                                y.ecn   
15273         14                                y.ecn   
17781         10                                n/</<   
17782         10                                n/</<   
17979         10                                M.ecn   
17980         10                                M.ecn   
18013         10                                n/</<   
18014         10                                n/</<   
18039         10                                n/</<   
18040         10                                n/</<   
18077         10                                n/</<   
18078         10                                n/</<   
18121         10                                n/</<   
18122         10                                n/</<   
18180         10                                n/</<   
18181         10                                n/</<   
18212         10                                n/</<   
18213         10                                n/</<   
18242         10                                n/</<   
18243         10                                n/</<   
18444          8   Fingerprint2.prototype.getCanvasFp   
18445          8   Fingerprint2.prototype.getCanvasFp   
19427          4                         resizeCanvas   
19428          4                         resizeCanvas   
19447          4                         resizeCanvas   
19448          4                         resizeCanvas   
20904          4                             b.update   
20905          4                             b.update   
20913          4                             b.update   
20914          4  

<b> Criteria 2 from Englehardt & Narayanan, 2016: </b> 

To be a fingerprinting candidate: "2.Text must be written to canvas with least two colors or
at least 10 distinct characters."

In [43]:
# js.symbol.value_counts()

In [44]:
# js[js.symbol == "CanvasRenderingContext2D.strokeStyle"]

In [17]:
import json 

def count_distinct_letters(text):
    if text!=None:
        t = json.loads(text, encoding='utf-8')['0']
        if not isinstance(t, int):
            return len(set(t))

In [18]:
CANVAS_WRITE_FUNCS = [
    "CanvasRenderingContext2D.fillText",
    "CanvasRenderingContext2D.strokeText",
    "CanvasRenderingContext2D.fill"
    ]

In [19]:
text = js[js.symbol.isin(CANVAS_WRITE_FUNCS)].arguments.dropna()
indexx = text.index
text = map(count_distinct_letters, text) 
res = pd.Series(text, index= indexx)
index_count_filter = res.where(res>=10).dropna().index

In [20]:
# js.iloc[index_count_filter][features_to_show]

crawl_id                                              func_name  \
650           14                        [87]/i</e.prototype.getCanvasFp   
653           14                        [87]/i</e.prototype.getCanvasFp   
2241           4                                  r.canvasFingerprint/<   
2245           4                                  r.canvasFingerprint/<   
2719           6                                e.prototype.getCanvasFp   
2725           6                                e.prototype.getCanvasFp   
5057          11                                                      v   
5060          11                                                      v   
5097          11                                                      v   
5102          11                                                      v   
5151          11                                                      v   
5154          11                                                      v   
5178          11                                                      v   
5181          11                                                      v   
5401          13                                                      v   
5404          13                                                      v   
5644           5                                                      v   
5647           5                                                      v   
5730           5                                                      v   
5733           5                                                      v   
5760           5                                                      v   
5763           5                                                      v   
17789         10                                                  n/</<   
17792         10                                                  n/</<   
17987         10                                                  M.ecn   
17990         10                                                  M.ecn   
18021         10                                                  n/</<   
18024         10                                                  n/</<   
18047         10                                                  n/</<   
18050         10                                                  n/</<   
18086         10                                                  n/</<   
18089         10                                                  n/</<   
18130         10                                                  n/</<   
18133         10                                                  n/</<   
18188         10                                                  n/</<   
18191         10                                                  n/</<   
18220         10                                                  n/</<   
18223         10                                                  n/</<   
18250         10                                                  n/</<   
18253         10                                                  n/</<   
18456          8                     Fingerprint2.prototype.getCanvasFp   
18459          8                     Fingerprint2.prototype.getCanvasFp   
29102         12                              fp2.prototype.getCanvasFp   
29105         12                              fp2.prototype.getCanvasFp   
30501          6                                                      I   
30511          6                                                      I   
31538         11                                                      v   
31541         11                                                      v   
41698         11                                                      v   
41701         11                                                      v   
45957          9                                                          
45960          9                                                          
56741          3                 

<b> Criteria 3 from Englehardt & Narayanan, 2016 </b>

To be a fingerprinting candidate: "3. The script should not call the save, restore, or addEventListener
methods of the rendering context."

In [21]:
CANVAS_FP_DO_NOT_CALL_LIST = ["CanvasRenderingContext2D.save",
                              "CanvasRenderingContext2D.restore",
                              "HTMLCanvasElement.addEventListener"]

In [22]:
# js[js.operation == "call"][js.arguments!=None].arguments.value_counts().head(15)
index_call_filter = js[~js.symbol.isin(CANVAS_FP_DO_NOT_CALL_LIST)].index
index_call_filter

Int64Index([     0,      1,      2,      3,      4,      5,      6,      7,
                 8,      9,
            ...
            501197, 501198, 501199, 501200, 501201, 501202, 501203, 501204,
            501205, 501206],
           dtype='int64', length=486982)

In [23]:
# js.iloc[index_call_filter][features_to_show]

crawl_id                                                    func_name  \
0              7                                                                
1              7                                                                
2              7                                                                
3             11                                                                
4              7                                                                
5              7                                                                
6              7                                                                
7              7                                                           mp   
8             11                                                                
9             11                                                                
10            11                                                                
11            11                                                                
12            11                                                                
13            11                                                           mp   
14             1                                                                
15             1                                                                
16             1                                                                
17             1                                                                
18             1                                                                
19             1                                                                
20             1                                                           mp   
21            11                                                         _.pj   
22             7                                                         _.pj   
23             1                                                         _.pj   
24            10                                                                
25            10                                                                
26            10                                                                
27            11                                                                
28            11                                                     s_Vb.Axb   
29             5                                     mw.storage.localStorage<   
30             5                                                                
31            11                                                     s_Vb.Rxb   
32            11                                                                
33             5                                                            n   
34            11                                                                
35            11                                                                
36            11                                                                
37            11                                                                
38            11                                                                
39            11                                                                
40            11                                                        s_Bda   
41            11                                               s_.isAvailable   
42            11                                               s_.isAvailable   
43            11                                               s_.isAvailable   
44            11                                               s_.isAvailable   
45             5                                                            n   
46            11                                                        s_Bda   
47            11                                                       s_.get   
48            11                       

In [52]:
# js[js.crawl_id==14].symbol.isin(CANVAS_FP_DO_NOT_CALL_LIST)

<b>Criteria 4 from Englehardt & Narayanan, 2016: </b>

To be a fingerprinting candidate: "4. The script extracts an image with toDataURL or with a
single call to getImageData that specifies an area with a
minimum size of 16px × 16px"

In [53]:
# js.symbol.value_counts()

In [24]:
CANVAS_READ_FUNCS = [
    "HTMLCanvasElement.toDataURL",
    "CanvasRenderingContext2D.getImageData"
    ]

In [25]:
# js[js.symbol.isin(CANVAS_READ_FUNCS)].arguments.dropna()

In [33]:
def check_dimensions(image):
    if image!=None:
        img = json.loads(image, encoding='utf-8')
        if len(img)>3:
            if img['2']>=16 and img['3']>=16:
                return image
        else: 
            return image

In [34]:
image = js[js.symbol.isin(CANVAS_READ_FUNCS)].arguments
indexx = image.index
image = map(check_dimensions, image)
res = pd.Series(image, index = indexx).dropna()
index_image_filter = res.index
index_image_filter

Int64Index([  3221,   6203,   6208,   6401,  39591,  39594,  39597,  39600,
             39603,  39606,
            ...
            339197, 339202, 339207, 345340, 415883, 422995, 443435, 460390,
            463353, 467632],
           dtype='int64', length=186)

In [55]:
# js

id  crawl_id  visit_id  \
0               1         7         7   
1               2         7         7   
2               3         7         7   
3               4        11        11   
4               5         7         7   
5               6         7         7   
6               7         7         7   
7               8         7         7   
8               9        11        11   
9              10        11        11   
10             11        11        11   
11             12        11        11   
12             13        11        11   
13             14        11        11   
14             15         1         1   
15             16         1         1   
16             17         1         1   
17             18         1         1   
18             19         1         1   
19             20         1         1   
20             21         1         1   
21             22        11        11   
22             23         7         7   
23             24         1         1   
24             25        10        10   
25             26        10        10   
26             27        10        10   
27             28        11        11   
28             29        11        11   
29             30         5         5   
30             31         5         5   
31             32        11        11   
32             33        11        11   
33             34         5         5   
34             35        11        11   
35             36        11        11   
36             37        11        11   
37             38        11        11   
38             39        11        11   
39             40        11        11   
40             41        11        11   
41             42        11        11   
42             43        11        11   
43             44        11        11   
44             45        11        11   
45             46         5         5   
46             47        11        11   
47             48        11        11   
48             49        11        11   
49             50         5         5   
50             51        11        11   
51             52         5         5   
52             53        11        11   
53             54         5         5   
54             55         5         5   
55             56         5         5   
56             57        11        11   
57             58         5         5   
58             59        11        11   
59             60        11        11   
60             61         5         5   
61             62        11        11   
62             63        11        11   
63             64         5         5   
64             65        11        11   
65             66        11        11   
66             67         5         5   
67             68        11        11   
68             69        11        11   
69             70        11        11   
70             71        11        11   
71             72        11        11   
72             73         5         5   
73             74         5         5   
74             75         5         5   
75             76         5         5   
76             77         5         5   
77             78         5         5   
78             79         5         5   
79             80        11        11   
80             81         5         5   
81             82         5         5   
82             83        11        11   
83             84        11        11   
84             85        11        11   
85             86        11        11   
86             87        11        11   
87             88        11        11   
88             89        11        11   
89             90        11        11   
90             91        11        11   
91             92        11        11   
92             93        11        11   
93             94        11        11   
94             95        11        11   
95             96        11        11   
96             97        11        11 

In [54]:
# js.operation.value_counts()

get            329145
call           122271
set             49788
set(failed)         3
Name: operation, dtype: int64

At least 2 criteria

In [59]:
lst = []

In [60]:
for i in range(len(js)):
    if i in index_call_filter and i in index_count_filter:
        lst.append(js.iloc[i])
    elif i in index_call_filter and i in index_size_filter:
        lst.append(js.iloc[i])
    elif i in index_call_filter and i in index_image_filter:
        lst.append(js.iloc[i])
    elif i in index_count_filter and i in index_size_filter:
        lst.append(js.iloc[i])
    elif i in index_count_filter and i in index_image_filter:
        lst.append(js.iloc[i])
    elif i in index_image_filter and i in index_size_filter:
        lst.append(js.iloc[i])

In [61]:
df = pd.DataFrame(lst)
len(df)

8122

In [44]:
fp_visit_id = []
for i in set(js.visit_id):
    cond1 = cond2 = cond3 = cond4 = False
    for j in js[js.visit_id==i].index:
        if j in index_size_filter:
            cond1 = True
        if j in index_count_filter:
            cond2 = True
        if j in index_call_filter:
            cond3 = True
        if j in index_image_filter:
            cond4 = True
    if cond1 and cond2 and cond3 and cond4:
        fp_visit_id.append(i)

In [51]:
fp_visit_id

[18, 19, 139, 201, 254, 382, 390, 407, 465, 512, 697, 874, 939]

In [52]:
# js[js.visit_id.isin(fp_visit_id)]

id  crawl_id  visit_id  \
2249      2250         5        19   
3218      3219        11        18   
3219      3220        11        18   
3220      3221        11        18   
3221      3222        11        18   
3222      3223        11        18   
3223      3224        11        18   
3224      3225        11        18   
3225      3226        11        18   
3226      3227        11        18   
3227      3228        11        18   
3228      3229        11        18   
3229      3230        11        18   
3230      3231        11        18   
3231      3232        11        18   
3232      3233        11        18   
3233      3234        11        18   
3234      3235        11        18   
3235      3236        11        18   
3236      3237        11        18   
3237      3238        11        18   
3238      3239        11        18   
3239      3240        11        18   
3240      3241        11        18   
3241      3242        11        18   
3242      3243        11        18   
3243      3244        11        18   
3244      3245        11        18   
3245      3246        11        18   
3246      3247        11        18   
3247      3248        11        18   
3248      3249        11        18   
3249      3250        11        18   
3250      3251        11        18   
3251      3252        11        18   
3252      3253        11        18   
3253      3254        11        18   
3254      3255        11        18   
3255      3256        11        18   
3256      3257        11        18   
3257      3258        11        18   
3258      3259        11        18   
3259      3260        11        18   
3260      3261        11        18   
3261      3262        11        18   
3262      3263        11        18   
3263      3264        11        18   
3264      3265        11        18   
3265      3266        11        18   
3266      3267        11        18   
3267      3268        11        18   
3268      3269        11        18   
3269      3270        11        18   
3270      3271        11        18   
3271      3272        11        18   
3272      3273        11        18   
3273      3274        11        18   
3274      3275        11        18   
3275      3276        11        18   
3276      3277        11        18   
3277      3278        11        18   
3278      3279        11        18   
3279      3280        11        18   
3280      3281        11        18   
3281      3282        11        18   
3282      3283        11        18   
3283      3284        11        18   
3284      3285        11        18   
3285      3286        11        18   
3286      3287        11        18   
3287      3288        11        18   
3288      3289        11        18   
3289      3290        11        18   
3290      3291        11        18   
3291      3292        11        18   
3292      3293        11        18   
3293      3294        11        18   
3294      3295        11        18   
3295      3296        11        18   
3296      3297        11        18   
3297      3298        11        18   
3298      3299        11        18   
3299      3300        11        18   
3300      3301        11        18   
3301      3302        11        18   
3302      3303        11        18   
3303      3304        11        18   
3304      3305        11        18   
3305      3306        11        18   
3306      3307        11        18   
3307      3308        11        18   
3308      3309        11        18   
3309      3310        11        18   
3310      3311        11        18   
3311      3312        11        18   
3312      3313        11        18   
3313      3314        11        18   
3314      3315        11        18   
3315      3316        11        18   
3316      3317        11        18   
3317      3318        11        18   
3318      3319        11        18   
3319      3320        11        18   
3320      3321        11        18   
3321      3322        

Each criterion separately

In [34]:
# lst1 = []
# lst2 = []
# lst3 = []
# lst4 = []

In [35]:
# for i in range(len(js)):
#     if i in index_size_filter:
#         lst1.append(js.iloc[i])
#     elif i in index_count_filter:
#         lst2.append(js.iloc[i])
#     elif i in index_call_filter:
#         lst3.append(js.iloc[i])
#     elif i in index_image_filter:
#         lst4.append(js.iloc[i])

In [36]:
# crt1 = pd.DataFrame(lst1)
# crt2 = pd.DataFrame(lst2)
# crt3 = pd.DataFrame(lst3)
# crt4 = pd.DataFrame(lst4)

In [37]:
# crt1[features_to_show]

All four criteria

In [38]:
# lst = []

In [39]:
# for i in range(len(js)):
#     if i in index_call_filter and i in index_count_filter and i in index_size_filter and i in index_image_filter:
#         lst.append(js.iloc[i])

In [40]:
# df = pd.DataFrame(lst)
# len(df)